In [1]:
import numpy as np
import pandas as pd
import re
import spacy
from catboost import CatBoostRegressor, Pool
from sklearn.model_selection import train_test_split

# Data loading

In [2]:
X_train = pd.read_csv("X_train.csv")
X_test = pd.read_csv("X_test.csv")
y_train = pd.read_csv("y_train.csv")

# Filling nans values

In [3]:
X_train.isnull().sum()

id                             0
name                           0
has_test                       0
response_letter_required       0
salary_from                 4032
salary_currency                0
salary_gross                 148
published_at                   0
created_at                     0
employer_name                  0
description                    1
area_id                        0
area_name                      0
dtype: int64

In [4]:
DataFrameTrain = y_train.merge(X_train) #взяла среднее отличие нижнего порога от верхнего в процентах для заполнения salary_from
DataFrameTrain['diff_percent'] = DataFrameTrain['salary_from'] / DataFrameTrain['salary_to']
median = DataFrameTrain['diff_percent'].median()
median

0.7142857142857143

In [5]:
for i in range(len(DataFrameTrain['salary_from'])):
	if pd.isna(DataFrameTrain['salary_from'][i]):
		DataFrameTrain['salary_from'][i] = DataFrameTrain['salary_to'][i] * median

DataFrameTrain = DataFrameTrain[DataFrameTrain['salary_from'] > 500] # посмотрела что всё что ниже 500 не имеет смысла (зп разработчика 150 рублей???)

/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/2562852900.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DataFrameTrain['salary_from'][i] = DataFrameTrain['salary_to'][i] * median
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/2562852900.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DataFrameTrain['salary_from'][i] = DataFrameTrain['salary_to'][i] * median
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/2562852900.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://

In [6]:
DataFrameTrain['description'] = DataFrameTrain['description'].fillna('') 
DataFrameTrain['salary_gross'] = DataFrameTrain['salary_gross'].fillna(False) # false было в два раза больше поэтому так

# Delete HTML tags

In [8]:
for i, text in enumerate(DataFrameTrain['description']):
	text = text.lower()
	pattern = re.compile('<.*?>')
	text = re.sub(pattern, '', text)
	DataFrameTrain['description'][i] = text

for i, text in enumerate(['description']):
	text = text.lower()
	pattern = re.compile('<.*?>')
	text = re.sub(pattern, '', text)
	X_test['description'][i] = text

/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/3559570609.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DataFrameTrain['description'][i] = text
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/3559570609.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DataFrameTrain['description'][i] = text
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/3559570609.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returnin

In [9]:
DataFrameTrain['description'][3]

'обязанности:обслуживание покупателей на кассе (наличный и безналичный расчет)выкладка товара в залеотслеживание сроков годности товарапроверка наличия ценниковконсультация покупателей в залетребования:ответственность, дисциплинированность, внимательностьусловия:график работы 5/2, 2/2, возможен неполный рабочий день, неполная рабочая неделявозможность подработки (работа по совместительству)социальные гарантии, оплата отпусков и больничных листовработа рядом с домомскидки в магазинах сетифирменная спецодеждавозможность профессионального и карьерного роста, корпоративное обучениекорпоративные мероприятия и конкурсы'

# NLP model loading

In [10]:
vectorizer_model = spacy.load("ru_core_news_lg")

# Vectorizing descriptions

In [15]:
DataFrameTrain['description_vectorized'] = DataFrameTrain['description'].apply(lambda x: vectorizer_model(x).vector)

DataFrameTrain[['descr_vec_' + str(i) for i in range(DataFrameTrain['description_vectorized'][0].shape[0])]] = (
	pd.DataFrame(DataFrameTrain['description_vectorized'].to_list(), index=DataFrameTrain.index))


X_test['description_vectorized'] = X_test['description'].apply(lambda x: vectorizer_model(x).vector)

X_test[['descr_vec_' + str(i) for i in range(X_test['description_vectorized'][0].shape[0])]] = (
	pd.DataFrame(X_test['description_vectorized'].to_list(), index=X_test.index))

/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_98821/2409689966.py:1: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  DataFrameTrain['description_vectorized'] = DataFrameTrain['description'].apply(lambda x: vectorizer_model(x).vector)


In [18]:
DataFrameTrain

id  salary_to                                               name  \
0      29083   200000.0  Менеджер по продажам (брокер) элитной городско...   
1      26052   170000.0  Product marketing manager / Продуктовый маркет...   
2      24055   120000.0                        Программист Python (Middle)   
3       4408    38000.0          Продавец-кассир (Москва, Вернадского, 93)   
4      16856    35000.0                              Дизайнер-визуализатор   
...      ...        ...                                                ...   
27929  16850   150000.0  Директор департамента по административной и ка...   
27930   6265    38000.0  Продавец-кассир (г Москва, ул Смольная, д 67 к 2)   
27931  11284    70000.0                            Младший аналитик данных   
27932    860   100000.0                      Копирайтер / контент менеджер   
27933  15795    60000.0                                      Гейм-дизайнер   

       has_test  response_letter_required    salary_from salary_currency  \
0         False                     False  142857.142857             RUR   
1         False                     False  120000.000000             RUR   
2         False                     False   85714.285714             RUR   
3         False                     False   33500.000000             RUR   
4         False                      True   30000.000000             RUR   
...         ...                       ...            ...             ...   
27929     False                     False  120000.000000             RUR   
27930     False                     False   33500.000000             RUR   
27931     False                     False   50000.000000             RUR   
27932     False                     False   60000.000000             RUR   
27933     False                     False   30000.000000             RUR   

       salary_gross            published_at              created_at  ...  \
0             False  2020-06-16 06:45:04+00  2020-06-16 06:45:04+00  ...   
1             False  2020-07-22 10:24:15+00  2020-07-22 10:24:15+00  ...   
2             False  2020-04-12 08:19:08+00  2020-04-12 08:19:08+00  ...   
3              True  2020-08-24 01:16:52+00  2020-08-24 01:16:52+00  ...   
4              True  2021-09-18 13:30:15+00  2021-09-18 13:30:15+00  ...   
...             ...                     ...                     ...  ...   
27929         False  2021-10-03 10:04:45+00  2021-10-03 10:04:45+00  ...   
27930          True  2020-09-07 00:32:00+00  2020-09-07 00:32:00+00  ...   
27931         False  2021-04-20 08:25:44+00  2021-04-20 08:25:44+00  ...   
27932         False  2020-11-15 11:12:07+00  2020-11-15 11:12:07+00  ...   
27933         False  2021-08-11 09:41:00+00  2021-08-11 09:41:00+00  ...   

      descr_vec_290 descr_vec_291  descr_vec_292 descr_vec_293  descr_vec_294  \
0          0.089024     -0.085020      -0.035552      0.021746       0.085075   
1          0.056654     -0.083819      -0.000456      0.005190       0.085936   
2          0.039222     -0.054167      -0.056502      0.026119       0.142602   
3          0.052223     -0.064120       0.062076      0.066182       0.042844   
4          0.079272     -0.082379       0.004172      0.026004       0.119526   
...             ...           ...            ...           ...            ...   
27929      0.065371     -0.053641       0.027304     -0.008650       0.024855   
27930      0.015871     -0.045833       0.042984      0.040510       0.029105   
27931      0.055293     -0.049482       0.054682     -0.001734       0.029002   
27932      0.059267     -0.084055       0.043352     -0.004953       0.012007   
27933      0.093138     -0.051120       0.033334     -0.008338       0.015093   

       descr_vec_295  descr_vec_296  descr_vec_297  descr_vec_298  \
0          -0.105378       0.004493      -0.039052       0.124997   
1          -0.151815      -0.003703      -0.046392       0.073128   
2          -0.147001       0.017640      -0.053799       0.088544  

# Features preparation

In [19]:
train_features = ['name', 'salary_from', 'area_id', 'employer_name']
cat_features = ['name', 'employer_name']
predict_features = ['salary_to']
for i in range(300):
	train_features.append('descr_vec_' + str(i))

# Model preparation

In [20]:
model = CatBoostRegressor(
	cat_features=cat_features,
	eval_metric='SMAPE',
	learning_rate=0.03,
	random_seed=42,
	verbose=False
)

train, test = train_test_split(DataFrameTrain, test_size=0.2, random_state=42)

train_pool = Pool(DataFrameTrain[train_features], DataFrameTrain[predict_features], cat_features=cat_features)
dev_pool = Pool(test[train_features], test[predict_features], cat_features=cat_features)

# Grid search :( very long

In [22]:
grid = {'depth': range(6),
		'iterations': [15000, 17000, 18000, 19000],
		'learning_rate':[0.029, 0.03, 0.031, 0.033]}

model.grid_search(param_grid=grid, X=train_pool, verbose=False)


bestTest = 54.82364332
bestIteration = 37

bestTest = 54.83111441
bestIteration = 36

bestTest = 54.81644294
bestIteration = 34

bestTest = 54.81355286
bestIteration = 32

bestTest = 54.82364332
bestIteration = 37

bestTest = 54.83111441
bestIteration = 36

bestTest = 54.81644294
bestIteration = 34

bestTest = 54.81355286
bestIteration = 32

bestTest = 54.82364332
bestIteration = 37

bestTest = 54.83111441
bestIteration = 36

bestTest = 54.81644294
bestIteration = 34

bestTest = 54.81355286
bestIteration = 32

bestTest = 54.82364332
bestIteration = 37

bestTest = 54.83111441
bestIteration = 36

bestTest = 54.81644294
bestIteration = 34

bestTest = 54.81355286
bestIteration = 32

bestTest = 25.37986313
bestIteration = 1246

bestTest = 25.37995634
bestIteration = 925

bestTest = 25.37155933
bestIteration = 1249

bestTest = 25.43007234
bestIteration = 962

bestTest = 25.37986313
bestIteration = 1246

bestTest = 25.37995634
bestIteration = 925

bestTest = 25.37155933
bestIteration = 1249


{'params': {'depth': 5, 'iterations': 15000, 'learning_rate': 0.033},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               45,
               46,


# Finally

In [23]:
predict = model.predict(X_test[train_features])
submit_id = X_test.id.to_list()
result = pd.DataFrame({'id': submit_id, 'salary_to': np.round(predict)})
result.to_csv('kate_submission.csv', index=False)